# 这只是一个完整项目的一部分 不能运行的 
- 可以从这个地址运行 [点击打开](https://www.kaggle.com/viyiviyi/sdwui-before)
---

In [ ]:
print('''
路径说明
*  可以使用 $install_path 或 {install_path} 来访问安装目录，写在字符串内也会生效
*  $output_path 或 {output_path} 可以访问输出目录
*  $input_path 或 {input_path} 可以访问输入目录 在kaggle是数据集根目录
*  如果链接了谷歌云盘，将会在云盘根目录创建 sdwebui 的文件夹，文件夹内的 Input 目录将会作为 输入目录 Output 将会作为输出目录

发布地址 https://www.kaggle.com/code/yiyiooo/stable-diffusion-webui-novelai

更新日志
*
*  23-07-26
*  增加可隐藏启动时的不重要信息 通过增加配置 [hidden_console_info = True] 开启
*  增加可自定义下载或链接文件到指定目录
*  配置方式：查看 https://www.kaggle.com/code/yiyiooo/stable-diffusion-webui-novelai 的 [其他文件列表]
*
*  23-07-22
*  更新了可自动同步收藏目录到 https://huggingface.co/ 的功能
*  可通过增加配置项 huggingface_token = "token" 和 huggingface_repo = “仓库id” 后使用此功能
*
*  23-07-18  
*  如果有两个GPU 第二个GPU将会启动api服务，可用api的方式调用，和webui互相独立，绘图时不会导致另外一边卡顿
*  通过/1/作为base url来访问这个api
*  没有启动两个webui是因为，很大概率爆内存
''')

In [ ]:
from pathlib import Path
import os
import time
import re
import subprocess
import threading
import sys
import socket
import torch
from typing import List

# 检查gpu是否存在
if torch.cuda.device_count() == 0:
    raise Exception('当前环境没有GPU')

install_path=f"{os.environ['HOME']}/sdwebui" # 安装目录
output_path=f"{os.environ['HOME']}/sdwebui/Output" # 输出目录 如果使用google云盘 会在google云盘增加sdwebui/Output
input_path = '/kaggle/input' # 输入目录

google_drive = '' 
# 连接谷歌云
try:
    if useGooglrDrive:
        from google.colab import drive
        drive.mount(f'~/google_drive')
        google_drive = f"{os.environ['HOME']}/google_drive/MyDrive"
        output_path = f'{google_drive}/sdwebui/Output'
        input_path = f'{google_drive}/sdwebui/Input'
        !mkdir -p {input_path}
        # 设置文件路径
        if setting_file== '/kaggle/working/configs/config.json':
            setting_file = os.path.join(output_path,'configs/config.json')
        if ui_config_file == '/kaggle/working/configs/ui-config.json':
            ui_config_file = os.path.join(output_path,'configs/ui-config.json')
        print('''
已经链接到谷歌云盘
云盘根目录/sdwebui/Output 被链接为输出目录，图片和设置文件将会保存在此文件夹
云盘根目录/sdwebui/Input 被链接为输入目录，环境变量名是 $input_path
        ''')
except:
    useGooglrDrive = False

!mkdir -p {install_path}
!mkdir -p {output_path}

os.environ['install_path'] = install_path
os.environ['output_path'] = output_path
os.environ['google_drive'] = google_drive
os.environ['input_path'] = input_path

def replace_path(input_str:str):
    return input_str.replace('$install_path',install_path)\
    .replace('{install_path}',install_path)\
    .replace('$input_path',input_path)\
    .replace('{input_path}',input_path)\
    .replace('$output_path',output_path)\
    .replace('{output_path}',output_path)

In [ ]:
# 模型目录 文件名称:链接的方式指定文件名
modelDirs = []+[replace_path(item.strip()) for item in 模型列表.split('\n') if item.strip() ]
# vae列表
modelVaeDirs = []+[replace_path(item.strip()) for item in VAE列表.split('\n') if item.strip()]
# 此配置内的目录下所有文件将加载到hypernetworks文件夹
hypernetworksModelDirs = []+[replace_path(item.strip()) for item in hypernetworks列表.split('\n') if item.strip()] 
# 此配置内的目录下所有文件将加载到embeddings文件夹
embeddingsModelDirs = [] +[replace_path(item.strip()) for item in embeddings列表.split('\n') if item.strip()]
# 此配置内的目录下所有文件将加载到Lora文件夹
loraModelDirs = []+[replace_path(item.strip()) for item in Lora列表.split('\n') if item.strip()] 

lyCORISModelDirs = []+[replace_path(item.strip()) for item in LyCORIS列表.split('\n') if item.strip()] 
# controlNet插件模型列表
controlNetModels=[] +[replace_path(item.strip()) for item in controlNet模型列表.split('\n') if item.strip()]
# 插件列表
extensions=[]+[replace_path(item.strip()) for item in 插件列表.split('\n') if item.strip()]
# 配置文件链接
linkHypernetworksDir=False # 链接 hypernetworks 目录到输出目录
linkEmbeddingsDir=False # 链接 embeddings 目录到输出目录
linkTextual_inversionDir=False # 链接 textual_inversion 目录到输出目录 如果需要保存训练过程的产出文件时建议开启

ngrokTokenFile = os.path.join(input_path,'configs/ngrok_token.txt') # 非必填 存放ngrokToken的文件的路径
frpcConfigFile = os.path.join(input_path,'configs/frpc_koishi.ini')  # 非必填 frp 配置文件
# ss证书目录 下载nginx的版本，把pem格式改成crt格式
frpcSSLFFlies =[os.path.join(input_path,'configs/koishi_ssl')]+[replace_path(item.strip()) for item in frpSSL文件.split('\n') if item.strip() ]
# frpc 文件目录 如果目录不存在，会自动下载，也可以在数据集搜索 viyiviyi/utils 添加
frpcExePath = os.path.join(input_path,'utils-tools/frpc')
# 其他需要加载的webui启动参数 写到【参数列表】这个配置去
otherArgs = ' '.join([replace_path(item.strip()) for item in 参数列表.split('\n') if item.strip()])

venvPath = os.path.join(input_path,'sd-webui-venv/venv.tar.bak') # 安装好的python环境 sd-webui-venv是一个公开是数据集 可以搜索添加

# 用于使用kaggle api的token文件 参考 https://www.kaggle.com/docs/api
# 此文件用于自动上传koishi的相关配置 也可以用于保存重要的输出文件
kaggleApiTokenFile = os.path.join(input_path,'configs/kaggle.json')

requirements = []

In [ ]:
# 这下面的是用于初始化一些值或者环境变量的，轻易别改
frpcStartArg = ''

frp配置文件或配置 = replace_path(frp配置文件或配置)
ngrok配置或文件地址 = replace_path(ngrok配置或文件地址)

!mkdir -p $install_path/configFiles
if Path(frp配置文件或配置.strip()).exists():
    frpcConfigFile = frp配置文件或配置.strip()
if not Path(frpcConfigFile).exists(): 
    if frp配置文件或配置.strip().startswith('-f'):
        frpcStartArg = frp配置文件或配置.strip()
    else:
        print('没有frpcp配置')
        useFrpc = False
else:
    os.system(f'cp -f {frpcConfigFile} {install_path}/configFiles/frpc_webui.ini')
    frpcConfigFile = f'{install_path}/configFiles/frpc_webui.ini'
    os.system(f'sed -i "s/local_port = .*/local_port = {webuiPort}/g" {frpcConfigFile}')
    frpcStartArg = f' -c {frpcConfigFile}'

ngrokToken=''
if Path(ngrok配置或文件地址.strip()).exists():
    ngrokTokenFile = ngrok配置或文件地址.strip()
if Path(ngrokTokenFile).exists():
    with open(ngrokTokenFile,encoding = "utf-8") as nkfile:
        ngrokToken = nkfile.readline()
elif not ngrok配置或文件地址.strip().startswith('/'):
    ngrokToken=ngrok配置或文件地址.strip()
    
if not Path(venvPath).exists():
    venvPath = os.path.join(input_path,'sd-webui-venv/venv.zip')


In [ ]:
def get_other_files():
    if '其他文件列表' not in globals():
        return {}
    other_flie_list = [replace_path(item.split('#')[0].strip()) for item in 其他文件列表.split('\n') if item.strip()]
    other_flie_list_store = {}
    other_flie_list_store_name='default'
    other_flie_list_store_list_cache=[]
    for item in other_flie_list:
        if item.startswith('[') and item.endswith(']'):
            if not other_flie_list_store_name == 'default':
                other_flie_list_store[other_flie_list_store_name]=other_flie_list_store_list_cache
                other_flie_list_store_list_cache = []
            other_flie_list_store_name = item[1:-1]
        else:
            other_flie_list_store_list_cache.append(item)
    other_flie_list_store[other_flie_list_store_name]=other_flie_list_store_list_cache
    return other_flie_list_store

In [ ]:
import os,sys,io
sys_sys_stdout = sys.stdout
class HiddenPrints:
    def __enter__(self):
        if 'hidden_console_info' not in globals(): return
        if hidden_console_info:
            self._stdout = sys.stdout
            sys.stdout = self._stringio = io.StringIO()

    def __exit__(self, *args):
        if 'hidden_console_info' not in globals(): return
        if hidden_console_info:
            sys.stdout = self._stdout

# kaggle public API

**不能使用%cd这种会改变当前工作目录的命令，会导致和其他线程冲突**

---

In [ ]:
# 安装kaggle的api token文件
def initKaggleConfig():
    if Path('~/.kaggle/kaggle.json').exists():
        return True
    if Path(kaggleApiTokenFile).exists():
        !mkdir -p ~/.kaggle/
        os.system('cp '+kaggleApiTokenFile+' ~/.kaggle/kaggle.json')
        !chmod 600 ~/.kaggle/kaggle.json
        return True
    print('缺少kaggle的apiToken文件，访问：https://www.kaggle.com/你的kaggle用户名/account 获取')
    return False

def getUserName():
    if not initKaggleConfig(): return
    import kaggle
    return kaggle.KaggleApi().read_config_file()['username']

def createOrUpdateDataSet(path:str,datasetName:str):
    if not initKaggleConfig(): return
    print('创建或更新数据集 '+datasetName)
    import kaggle
    os.system('mkdir -p $install_path/kaggle_cache')
    os.system('rm -rf $install_path/kaggle_cache/*')
    datasetDirPath = install_path+'/kaggle_cache/'+datasetName
    os.system('mkdir -p '+datasetDirPath)
    os.system('cp -f '+path+' '+datasetDirPath+'/')
    username = getUserName()
    print("kaggle username:"+username)
    datasetPath = username+'/'+datasetName
    datasetList = kaggle.api.dataset_list(mine=True,search=datasetPath)
    print(datasetList)
    if len(datasetList) == 0 or datasetPath not in [str(d) for d in datasetList]: # 创建 create
        os.system('kaggle datasets init -p' + datasetDirPath)
        metadataFile = datasetDirPath+'/dataset-metadata.json'
        os.system('sed -i s/INSERT_TITLE_HERE/'+ datasetName + '/g ' + metadataFile)
        os.system('sed -i s/INSERT_SLUG_HERE/'+ datasetName + '/g ' + metadataFile)
        os.system('cat '+metadataFile)
        os.system('kaggle datasets create -p '+datasetDirPath)
        print('create database done')
    else:
        kaggle.api.dataset_metadata(datasetPath,datasetDirPath)
        kaggle.api.dataset_create_version(datasetDirPath, 'auto update',dir_mode='zip')
        print('upload database done')

def downloadDatasetFiles(datasetName:str,outputPath:str):
    if not initKaggleConfig(): return
    print('下载数据集文件 '+datasetName)
    import kaggle
    username = getUserName()
    datasetPath = username+'/'+datasetName
    datasetList = kaggle.api.dataset_list(mine=True,search=datasetPath)
    if datasetPath not in [str(d) for d in datasetList]:
        return False
    os.system('mkdir -p '+outputPath)
    kaggle.api.dataset_download_files(datasetPath,path=outputPath,unzip=True)
    return True



# 同步文件夹到 huggingface


In [ ]:
# 文件夹与 huggingface 同步
if 'huggingface_token' in locals() and 'huggingface_repo' in locals():
    requirements.append('watchdog')
    requirements.append('huggingface_hub')


huggingface_is_init = False

def init_huggingface():
    if 'huggingface_token' not in globals() or 'huggingface_repo' not in globals():
        print('请增加配置项 huggingface_token = "token" 和 huggingface_repo = “仓库id” 后使用 huggingface 功能')
        return False
    global huggingface_is_init
    from huggingface_hub  import HfApi,login,snapshot_download
    token = replace_path(huggingface_token)
    if Path(token).exists():
        with open(token,encoding = "utf-8") as nkfile:
            token = nkfile.readline()
    if not token.startswith('hf_'):
        print('huggingface token 不正确，请将 token 或 仅存放token 的txt文件路径填入 huggingface_token 配置')
        return False
    login(token)
    huggingface_is_init = True
    return True


def download_huggingface_repo(repo_id:str,dist_directory:str=None,repo_type='dataset',callback=None):
    if not huggingface_is_init:
        print('huggingface 相关功能未初始化 请调用 init_huggingface() 初始化')
        
    if not dist_directory:
        dist_directory = f'{install_path}/stable-diffusion-webui/log'
    
    from huggingface_hub  import HfApi,login,snapshot_download
    
    api = HfApi()
    
    print('下载收藏的图片')
    snapshot_download(repo_id = huggingface_repo,
                      local_dir = dist_directory,
                      local_dir_use_symlinks = "auto",
                      token=True,
                      repo_type=repo_type
                     )
    if callback:
        callback()

def start_sync_log_to_huggingface(repo_id:str,directory_to_watch:str=None,repo_type='dataset'):
    if not huggingface_is_init:
        print('huggingface 相关功能未初始化 请调用 init_huggingface() 初始化')
    
    from watchdog.observers import Observer
    from watchdog.events import FileSystemEventHandler
    from huggingface_hub  import HfApi,login,snapshot_download
    
    # 配置监视的目录和 Hugging Face 仓库信息
    class FileChangeHandler(FileSystemEventHandler):
        def __init__(self, api, repo_id, repo_type):
            self.api = api
            self.repo_id = repo_id
            self.repo_type = repo_type
        def on_created(self, event):
            if not event.is_directory:
                # 上传新文件到 Hugging Face 仓库
                file_path = event.src_path
                file_name = os.path.basename(file_path)
                if file_name[-4:] not in ['.png','.jpg','.txt']: return
                try:
                    self.api.upload_file(
                        path_or_fileobj=file_path,
                        path_in_repo=file_path.replace(directory_to_watch,''),
                        repo_id=self.repo_id,
                        repo_type=self.repo_type,
                    )
                except Error as error:
                    print(error)

        def on_deleted(self, event):
            if not event.is_directory:
                # 从 Hugging Face 仓库删除文件
                file_path = event.src_path
                file_name = os.path.basename(file_path)
                if file_name[-4:] not in ['.png','.jpg','.txt']: return
                try:
                    self.api.delete_file(
                        path_in_repo=file_path.replace(directory_to_watch,''),
                        repo_id=self.repo_id,
                        repo_type=self.repo_type,
                        )
                except Error as error:
                    print(error)

        def on_modified(self, event):
            if not event.is_directory:
                # 更新 Hugging Face 仓库中的文件
                file_path = event.src_path
                file_name = os.path.basename(file_path)
                if file_name[-4:] not in ['.png','.jpg','.txt']: return
                try:
                    self.api.upload_file(
                        path_or_fileobj=file_path,
                        path_in_repo=file_path.replace(directory_to_watch,''),
                        repo_id=self.repo_id,
                        repo_type=self.repo_type,
                    )
                except Error as error:
                    print(error)

        def on_moved(self, event):
            if not event.is_directory:
                file_path = event.dest_path
                file_name = os.path.basename(file_path)
                if file_name[-4:] not in ['.png','.jpg','.txt']: return
                if event.dest_path.startswith(directory_to_watch):
                    try:
                        self.api.upload_file(
                            path_or_fileobj=file_path,
                            path_in_repo=file_path.replace(directory_to_watch,''),
                            repo_id=self.repo_id,
                            repo_type=self.repo_type,
                        )
                    except Error as error:
                        print(error)

    api = HfApi()
    
    if not directory_to_watch:
        directory_to_watch = f'{install_path}/stable-diffusion-webui/log'
    # 创建观察者对象并注册文件变化处理程序
    event_handler = FileChangeHandler(api,repo_id,repo_type)
    observer = Observer()
    observer.schedule(event_handler, directory_to_watch, recursive=True)

    # 启动观察者
    observer.name = "solo_directory_to_watch"
    print(f'启动收藏图片文件夹监听，并自动同步到 huggingface {repo_type} : {repo_id}')
    observer.start()

# 工具函数
**不能使用%cd这种会改变当前工作目录的命令，会导致和其他线程冲突**

---

一般工具函数

In [ ]:
# 绕过 os.systen 的限制执行命令
def run(shell:str,shellName=''):
    if shellName == '': shellName = str(time.time())
    !mkdir -p $install_path/run_cache
    with open(install_path+'/run_cache/run_cache.'+shellName+'.sh','w') as sh:
        sh.write(shell)
    !bash {install_path}/run_cache/run_cache.{shellName}.sh

# 连接多个路径字符串 让路径在shell命令中能正常的执行
def pathJoin(*paths:str):
    pathStr = ''
    for p in paths:
        pathStr += '"'+p+'"'
    pathStr = '"*"'.join(pathStr.split('*'))
    pathStr = '"$"'.join(pathStr.split('$'))
    pathStr = '"("'.join(pathStr.split('('))
    pathStr = '")"'.join(pathStr.split(')'))
    pathStr = '"{"'.join(pathStr.split('{'))
    pathStr = '"}"'.join(pathStr.split('}'))
    pathStr = re.sub(r'""','',pathStr)
    pathStr = re.sub(r'\*{2,}','"',pathStr)
    pathStr = re.sub(r'/{2,}','/',pathStr)
    pathStr = re.sub(r'/\./','/',pathStr)
    return pathStr

# 判断路径是不是一个文件或者可能指向一些文件
def pathIsFile(path):
    if Path(path).is_file():
        return True
    if re.search(r'\.(ckpt|safetensors|png|jpg|txt|pt|pth|json|yaml|\*)$',path):
        return True
    return False

def echoToFile(content:str,path:str):
    with open(path,'w') as sh:
        sh.write(content)

# ngrok
def startNgrok(ngrokToken:str,ngrokLocalPort:int):
    from pyngrok import conf, ngrok
    try:
        conf.get_default().auth_token = ngrokToken
        conf.get_default().monitor_thread = False
        ssh_tunnels = ngrok.get_tunnels(conf.get_default())
        if len(ssh_tunnels) == 0:
            ssh_tunnel = ngrok.connect(ngrokLocalPort)
            print('ngrok 访问地址：'+ssh_tunnel.public_url)
        else:
            print('ngrok 访问地址：'+ssh_tunnels[0].public_url)
    except:
        print('启动ngrok出错')
        
def startFrpc(name,configFile):
    run(f'''
cd $install_path/frpc/
$install_path/frpc/frpc {configFile}
        ''',name)
        
def installProxyExe():
    if useFrpc:
        print('安装frpc')
        !mkdir -p $install_path/frpc
        if Path(frpcExePath).exists():
            os.system(f'cp -f -n {frpcExePath} $install_path/frpc/frpc')
        else:
            !wget "https://huggingface.co/datasets/ACCA225/Frp/resolve/main/frpc" -O $install_path/frpc/frpc
        
        for ssl in frpcSSLFFlies:
            if Path(ssl).exists():
                os.system('cp -f -n '+pathJoin(ssl,'/*')+' $install_path/frpc/')
        !chmod +x $install_path/frpc/frpc
        !$install_path/frpc/frpc -v
    if useNgrok:
        %pip install pyngrok

def startProxy():
    if useNgrok:
        startNgrok(ngrokToken,webuiPort)
    if useFrpc:
        startFrpc('frpc_proxy',frpcStartArg)

    
def zipPath(path:str,zipName:str,format='tar'):
    if path.startswith('$install_path'):
        path = path.replace('$install_path',install_path)
    if path.startswith('$output_path'):
        path = path.replace('$install_path',output_path)
    if not path.startswith('/'):
        path = pathJoin(install_path,'/stable-diffusion-webui','/',path)
    if Path(path).exists():
        if 'tar' == format:
            os.system('tar -cf $output_path/'+ zipName +'.tar -C '+ path +' . ')
        elif 'gz' == format:
            os.system('tar -czf $output_path/'+ zipName +'.tar.gz -C '+ path +' . ')
        return
    print('指定的目录不存在：'+path)

        
def check_service(host, port):
    try:
        socket.create_connection((host, port), timeout=5)
        return True
    except socket.error:
        return False

文件下载工具

In [ ]:
import os
import re
import requests

def download_file(url, filename, path,cache_path = ''):
    # 获取文件的真实文件名
    if not filename:
        with requests.get(url, stream=True) as r:
            if 'Content-Disposition' in r.headers:
                filename = r.headers['Content-Disposition'].split('filename=')[1].strip('"')
            r.close()
    filename = re.sub(r'[\\/:*?"<>|;]', '', filename)
    # 拼接文件的完整路径
    filepath = os.path.join(path, filename)
    if cache_path:
        cache_path = os.path.join(cache_path, filename)
    # 判断文件是否已存在
    if os.path.exists(filepath):
        print(f'{filename} already exists in {path}')
        return
    if cache_path and os.path.exists(cache_path):
        !ln -s -f {cache_path} {filepath}
    # 下载文件
    with requests.get(url, stream=True) as r:
        r.raise_for_status()
        with open(filepath, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)
    print(f'{filename} has been downloaded to {path}')
    
# 加入文件到下载列表
def putDownloadFile(url:str,distDir:str,file_name:str=None):
    if re.match(r'^[^:]+:(https?|ftps?)://', url, flags=0):
        file_name = re.findall(r'^[^:]+:',url)[0][:-1]
        url = url[len(file_name)+1:]
    if not re.match(r'^(https?|ftps?)://',url):
        return
    file_name = re.sub(r'\s+','_',file_name or '')
    dir = str(hash(url)).replace('-','')
    down_dir = f'{install_path}/down_cache/{dir}'
    !mkdir -p {down_dir}
    return [url,file_name,distDir,down_dir]

def get_file_size_in_gb(file_path):
    size_in_bytes = Path(file_path).stat().st_size
    size_in_gb = size_in_bytes / (1024 ** 3)
    return '%.2f' % size_in_gb
    
# 下载文件
def startDownloadFiles(download_list):
    print('下载列表:\n','\n'.join([f'{item[0]} -> {item[2]}/{item[1]}' for item in download_list]))
    dist_list = []
    for dow_f in download_list:
        !mkdir -p {dow_f[3]}
        print('下载 名称：',dow_f[1],'url：',dow_f[0])
        download_file(dow_f[0],dow_f[1],dow_f[2],dow_f[3])
        



NGINX 反向代理

In [ ]:

# nginx 反向代理配置文件
def localProxy():
    conf = '''
server
{
    listen '''+str(webuiPort)+''';
    listen [::]:'''+str(webuiPort)+''';
    server_name 127.0.0.1 localhost 0.0.0.0 "";
    
    if ($request_method = OPTIONS) {
        return 200;
    }
    fastcgi_send_timeout                 10m;
    fastcgi_read_timeout                 10m;
    fastcgi_connect_timeout              10m;
    location /1/
    {
        proxy_pass http://127.0.0.1:'''+str(webuiPort+2)+'''/;
        # add_header Set-Cookie "subpath=1; expires=0; Path=/";
        # proxy_set_header Set-Cookie "subpath=1; expires=0; Path=/";
        proxy_set_header Host $host;
        proxy_set_header X-Real-IP $remote_addr;
        proxy_set_header X-Forwarded-For $proxy_add_x_forwarded_for;
        proxy_set_header REMOTE-HOST $remote_addr;
        proxy_set_header   Upgrade $http_upgrade;
        proxy_set_header   Connection upgrade;
        proxy_http_version 1.1;
        proxy_connect_timeout 10m;
        proxy_read_timeout 10m;
    }
    location /
    {
        set $proxy_url http://127.0.0.1:'''+str(webuiPort+1)+''';
        # if ($cookie_subpath = "1") {
        #    set $proxy_url  http://127.0.0.1:'''+str(webuiPort+2)+''';
        # }
        proxy_pass $proxy_url;
        proxy_set_header Host $host;
        proxy_set_header X-Real-IP $remote_addr;
        proxy_set_header X-Forwarded-For $proxy_add_x_forwarded_for;
        proxy_set_header REMOTE-HOST $remote_addr;
        proxy_set_header   Upgrade $http_upgrade;
        proxy_set_header   Connection upgrade;
        proxy_http_version 1.1;
        proxy_connect_timeout 10m;
        proxy_read_timeout 10m;
    }
}
'''
    echoToFile(conf,'/etc/nginx/conf.d/proxy_nginx.conf')
    if not check_service('localhost',webuiPort):
        !nginx -c /etc/nginx/nginx.conf
    !nginx -s reload
    

线程清理工具

In [ ]:
import inspect
import ctypes

def _async_raise(tid, exctype):
    """raises the exception, performs cleanup if needed"""
    tid = ctypes.c_long(tid)
    if not inspect.isclass(exctype):
        exctype = type(exctype)
    res = ctypes.pythonapi.PyThreadState_SetAsyncExc(tid, ctypes.py_object(exctype))
    if res == 0:
        raise ValueError("invalid thread id")
    elif res != 1:
        # """if it returns a number greater than one, you're in trouble,
        # and you should call it again with exc=NULL to revert the effect"""
        ctypes.pythonapi.PyThreadState_SetAsyncExc(tid, None)
        raise SystemError("PyThreadState_SetAsyncExc failed")

def stop_thread(thread):
    _async_raise(thread.ident, SystemExit)

def stop_solo_threads():
    # 获取当前所有活动的线程
    threads = threading.enumerate()
    # 关闭之前创建的子线程
    for thread in threads:
        if thread.name.startswith('solo_'):
            print(thread.name)
            try:
                stop_thread(thread)
            except socket.error:
                print(f'结束进程：{thread.name} 执行失败')

# webui 安装和配置函数
---

In [ ]:
envInstalled=False
extensionsDone=False

#安装webui
def install():
    print('安装webui')
    %cd $install_path
    with HiddenPrints():
        for requirement in requirements:
            !pip install {requirement}
    if reLoad:
        !rm -rf stable-diffusion-webui
    if Path("stable-diffusion-webui").exists():
        %cd $install_path/stable-diffusion-webui/
        !git checkout .
        !git pull
    else:
        if mobileOptimize:
            !git clone https://github.com/viyiviyi/stable-diffusion-webui.git stable-diffusion-webui -b local  # 修改了前端界面，手机使用更方便
        else:
            !git clone https://github.com/AUTOMATIC1111/stable-diffusion-webui stable-diffusion-webui
    %cd {install_path}/stable-diffusion-webui
    print('安装webui 完成')

# 链接输出目录
def link_dir():
    print('链接输出目录')
    # 链接输出目录 因为sd被部署在了stable-diffusion-webui目录，运行结束后为了方便下载就只有outputs目录放在output_path/目录下
    !mkdir -p $output_path/outputs
    !rm -rf $install_path/stable-diffusion-webui/outputs
    !ln -s -r $output_path/outputs $install_path/stable-diffusion-webui/ # 输出目录
    !mkdir -p $output_path/log
    !rm -rf $install_path/stable-diffusion-webui/log
    !ln -s -r $output_path/log $install_path/stable-diffusion-webui/
    # 链接 hypernetworks 目录
    if linkHypernetworksDir:
        !rm -rf $install_path/stable-diffusion-webui/models/hypernetworks
        !mkdir -p $output_path/hypernetworks
        !ln -s -r $output_path/hypernetworks $install_path/stable-diffusion-webui/models/
    # 链接 embeddings 目录
    if linkEmbeddingsDir:
        !rm -rf $install_path/stable-diffusion-webui/embeddings
        !mkdir -p $output_path/embeddings
        !ln -s -r $output_path/embeddings $install_path/stable-diffusion-webui/
    # 链接训练输出目录 文件夹链接会导致功能不能用
    if linkTextual_inversionDir:
        !rm -rf $install_path/stable-diffusion-webui/textual_inversion
        !mkdir -p $output_path/textual_inversion/
        !ln -s -r $output_path/textual_inversion $install_path/stable-diffusion-webui/
    print('链接输出目录 完成')
    
def link_or_download_flie(skip_down:bool,store:dict[str,List[str]]):
    download_list = []
    for dist_dir in store.keys():
        dist_path = os.path.join(f'{install_path}/stable-diffusion-webui',dist_dir)
        !mkdir -p {dist_path}
        for path in store[dist_dir]:
            if 'https://' in path or 'http://' in path:
                if skip_down:
                    continue
                download_list.append(putDownloadFile(path,dist_path))
            elif pathIsFile(path):
                os.system(('cp -n' if enableLoadByCopy else 'ln -s')+' -f '+ pathJoin(path) +f' {dist_path}')
            else:
                os.system(('cp -n' if enableLoadByCopy else 'ln -s')+' -f '+ pathJoin(path,'/*.*') +f' {dist_path}')
        !rm -f {dist_path}/\*.* 
    startDownloadFiles(download_list)
        
# 链接模型文件
def load_models(skip_url=False):
    print(('复制' if enableLoadByCopy else '链接') + '模型文件')
    if enableLoadByCopy:
        print('如果出现 No such file or directory 错误，可以忽略')
    store = get_other_files()
    store['models/Stable-diffusion'] = modelDirs + (store['models/Stable-diffusion'] if 'models/Stable-diffusion' in store else [])
    store['models/hypernetworks'] = hypernetworksModelDirs + (store['models/hypernetworks'] if 'models/hypernetworks' in store else [])
    store['models/embeddings'] = embeddingsModelDirs + (store['models/embeddings'] if 'models/embeddings' in store else [])
    store['models/Lora'] = loraModelDirs + (store['models/Lora'] if 'models/Lora' in store else [])
    store['models/LyCORIS'] = lyCORISModelDirs + (store['models/LyCORIS'] if 'models/LyCORIS' in store else [])
    store['models/VAE'] = modelVaeDirs + (store['models/VAE'] if 'models/VAE' in store else [])
    store['extensions/sd-webui-controlnet/models'] = controlNetModels + (store['extensions/sd-webui-controlnet/models'] if 'extensions/sd-webui-controlnet/models' in store else [])
    link_or_download_flie(skip_url,store)
    print(('复制' if enableLoadByCopy else '链接') + '模型文件 完成')

#安装依赖
def install_dependencies():
    print('安装webui需要的python环境')
    global envInstalled
    global venvPath
    print(venvPath)
    
    with HiddenPrints():
        %env TF_CPP_MIN_LOG_LEVEL=1
        !apt -y update -qq
        !wget http://launchpadlibrarian.net/367274644/libgoogle-perftools-dev_2.5-2.2ubuntu3_amd64.deb
        !wget https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/google-perftools_2.5-2.2ubuntu3_all.deb
        !wget https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/libtcmalloc-minimal4_2.5-2.2ubuntu3_amd64.deb
        !wget https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/libgoogle-perftools4_2.5-2.2ubuntu3_amd64.deb
        !apt -y install -qq libunwind8-dev
        !dpkg -i *.deb
        %env LD_PRELOAD=libtcmalloc.so
        !rm *.deb
        !sudo apt install nginx -y

    sh = f'cd {install_path}/stable-diffusion-webui\n'
    if str(sys.version).startswith('3.8') or str(sys.version).startswith('3.9') or str(sys.version).startswith('3.10'):
        sh += 'python -m venv venv\n'
    else:
        sh += '''
add-apt-repository ppa:deadsnakes/ppa -y
apt update
apt install python3.10 -y
python3.10 -m venv venv
'''
    if quickStart:
        if not Path(venvPath).exists():
            !mkdir -p {install_path}/venv_cache
            if not Path(f'{install_path}/venv_cache/venv.tar.bak').exists():
                download_file('https://huggingface.co/viyi/sdwui/resolve/main/venv.zip','venv.zip',f'{install_path}/venv_cache')
            !unzip {install_path}/venv_cache/venv.zip -d {install_path}/venv_cache
            venvPath = f'{install_path}/venv_cache/venv.tar.bak'
            !rm -rf {install_path}/venv_cache/venv.zip
        elif venvPath.endswith('.zip'):
            !mkdir -p {install_path}/venv_cache
            !unzip {venvPath} -d {install_path}/venv_cache
            venvPath = f'{install_path}/venv_cache/venv.tar.bak'

        sh += 'echo "unzip venv"\n'
        sh += f'tar -xf {venvPath} -C ./venv\n'
    sh += '\n'
    with HiddenPrints():
        run(sh,'dependencies')
    if not Path(f'{install_path}/stable-diffusion-webui/venv/bin/pip').exists():
        !curl https://bootstrap.pypa.io/get-pip.py -o get-pip.py
        with HiddenPrints():
            !{install_path}/stable-diffusion-webui/venv/bin/python3 get-pip.py

    !{install_path}/stable-diffusion-webui/venv/bin/python3 -V
    !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip -V

    if not quickStart or not Path(venvPath).exists():
        with HiddenPrints():
            !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip install -U torch==2.0.0+cu117 torchvision==0.15.1+cu117 torchaudio==2.0.1 --index-url https://download.pytorch.org/whl/cu117
            !{install_path}/stable-diffusion-webui/venv/bin/python3 -m pip install -U open-clip-torch xformers==0.0.19

    envInstalled = True
    print('安装webui需要的python环境 完成')

# 安装插件
def install_extensions():
    global extensionsDone
    print('安装插件')
    sh = 'mkdir -p $install_path/stable-diffusion-webui/extensions \n'
    sh = 'mkdir -p $install_path/cache/extensions \n'
    sh += 'cd $install_path/cache/extensions \n'
    for ex in extensions:
        sh += 'git clone ' + ex + ' \n'
    sh += 'rsync -a $install_path/cache/extensions/* $install_path/stable-diffusion-webui/extensions \n'
    sh += 'cd ../ && rm -rf $install_path/cache/extensions \n'
    with HiddenPrints():
        run(sh,'extensions')
        extensionsDone = True
    print('安装插件 完成')
    
# 个性化配置 
def use_config():
    print('使用自定义配置 包括tag翻译 \n')
    %cd $install_path/stable-diffusion-webui
    !mkdir -p tmp
    %cd tmp
    !git clone {webui_settings} sd-configs
    !cp -rf sd-configs/dist/* $install_path/stable-diffusion-webui
    if not Path(ui_config_file).exists(): # ui配置文件
        !mkdir -p {ui_config_file[0:ui_config_file.rfind('/')]}
        os.system('cp -f -n $install_path/stable-diffusion-webui/ui-config.json '+ui_config_file)
    if not Path(setting_file).exists(): # 设置配置文件
        !mkdir -p {setting_file[0:setting_file.rfind('/')]}
        os.system('cp -f -n $install_path/stable-diffusion-webui/config.json '+setting_file)

def checkDefaultModel():
    print('检查默认模型文件是否存在 \n')
    global usedCkpt
    if usedCkpt is not None and usedCkpt != '': # 设置启动时默认加载的模型
        if '.' in usedCkpt:
            if '/' in usedCkpt:
                usedCkpt = usedCkpt
            else:
                usedCkpt = install_path + '/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt
        else:
            for x in ['.ckpt','.safetensors']:
                if Path(install_path+'/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt+x).exists():
                    usedCkpt = install_path+'/stable-diffusion-webui/models/Stable-diffusion/' + usedCkpt+x
                    break
    if Path(usedCkpt).exists():
        return True
    else:
        if Path(usedCkpt).is_symlink():
            print('模型文件真实地址：'+os.readlink(usedCkpt))
        return False

def copy_last_log_to_images():
    print('复制编号最大的一张收藏图到输出目录，用于保持编号，否则会出现收藏的图片被覆盖的情况')
    img_list = os.listdir(f'{install_path}/stable-diffusion-webui/log/images')
    last_img_path = ''
    last_img_num = 0
    for img in img_list:
        if re.findall(r'^\d+-',str(img)):
            num = int(re.findall(r'^\d+-',str(img))[0][:-1])
            if num > last_img_num:
                last_img_path = img
                last_img_num = num
    print(f'{install_path}/stable-diffusion-webui/log/images/{last_img_path} {install_path}/stable-diffusion-webui/outputs/txt2img-images')
    !mkdir -p {install_path}/stable-diffusion-webui/outputs/txt2img-images
    !cp -f {install_path}/stable-diffusion-webui/log/images/{last_img_path} {install_path}/stable-diffusion-webui/outputs/txt2img-images/
    
    print(f'{install_path}/stable-diffusion-webui/log/images/{last_img_path} {install_path}/stable-diffusion-webui/outputs/img2img-images')
    !mkdir -p {install_path}/stable-diffusion-webui/outputs/img2img-images
    !cp -f {install_path}/stable-diffusion-webui/log/images/{last_img_path} {install_path}/stable-diffusion-webui/outputs/img2img-images/
            
    
def start_webui(i):
    # 只要不爆内存，其他方式关闭后会再次重启 访问地址会发生变化
    print(i,'--port',str(webuiPort+1+i))
    if i>0:
        print(f'使用第{i+1}张显卡启动第{i+1}个webui，通过frpc或nrgok地址后加/{i}/进行访问（不能使用同一个浏览器）')
    if useFrpc:
        while True:
            !venv/bin/python3 launch.py --device-id={i} --port {str(webuiPort+1+i)} {'' if i ==0 else '--nowebui'} # {'' if i == 0 else '--subpath=/'+str(i)}
            print('5秒后重启webui')
            time.sleep(5)
    else:
        !venv/bin/python3 launch.py --device-id={i} --port {str(webuiPort+1+i)} {'' if i ==0 else '--nowebui'} # {'' if i == 0 else '--subpath=/'+str(i)}
    
# 启动
def start():
    print('启动webui')
    %cd $install_path/stable-diffusion-webui
    args = '' # ' --port=' + str(webuiPort+1)
    if not disableShared:
        args += ' --share'
    if onlyApi:
        args += ' --nowebui'
    if ui_config_file is not None and ui_config_file != '' and Path(ui_config_file).exists(): # ui配置文件
        args += ' --ui-config-file=' + pathJoin(ui_config_file)
    if setting_file is not None and setting_file != '' and Path(setting_file).exists(): # 设置配置文件
        args += ' --ui-settings-file=' + pathJoin(setting_file)
    if not checkDefaultModel():
        print('默认模型文件不存在，请检查配置：'+usedCkpt)
    else:
        args += ' --ckpt='+ pathJoin(usedCkpt)
    if vaeHalf is False: 
        args += ' --no-half-vae'
    if modelHalf is False:
        args += ' --no-half'
    if consoleProgressbars is False:
        args += ' --disable-console-progressbars'
    if consolePrompts is True:
        args += ' --enable-console-prompts'
    args += ' ' + otherArgs
    os.environ['COMMANDLINE_ARGS']=args
    !echo COMMANDLINE_ARGS=$COMMANDLINE_ARGS
    %env REQS_FILE=requirements.txt
    
    threads = []
    for i in range(torch.cuda.device_count()):
        thread = threading.Thread(target = start_webui, name='solo_start_webui_'+str(i), daemon=True,args=([i]))
        thread.start()
        threads.append(thread)
        while thread.is_alive() and not check_service('localhost',str(webuiPort+1+i)): # 当当前服务启动完成才允许退出此次循环
            time.sleep(10)
        time.sleep(5)
    for thread in threads:
        thread.join()

# 入口函数
---

In [ ]:

# 启动非webui相关的的内容，加快启动速度
def main():
    global envInstalled
    global extensionsDone
    global huggingface_is_init
    startTicks = time.time()
    isInstall = True if os.getenv('IsInstall','False') == 'True' else False
    if isInstall is False or reLoad: 
        print('启动 安装webui和运行环境')
        install()
        link_dir()
        init_huggingface()
        if enableThread:
            threading.Thread(target = install_extensions,daemon=True, name='solo_install_extensions').start()
            threading.Thread(target = load_models,daemon=True).start()
            threading.Thread(target = install_dependencies,daemon=True, name='solo_install_dependencies').start()
            if huggingface_is_init:
                threading.Thread(target = download_huggingface_repo,daemon=True,
                                 args=([huggingface_repo]),
                                 kwargs={"callback":copy_last_log_to_images},
                                 name='solo_download_huggingface_repo').start()

        else:
            install_extensions()
            load_models()
            install_dependencies()
            if huggingface_is_init:
                download_huggingface_repo(huggingface_repo,callback=copy_last_log_to_images)
        t = 0
        while not envInstalled or not extensionsDone:
            if t%10==0:
                print('等待python环境和插件安装...')
            t = t+1
            time.sleep(1)
        use_config()
        installProxyExe()
        os.environ['IsInstall'] = 'True'
    else:
        envInstalled = True
        extensionsDone = True
    sys.stdout = sys_sys_stdout
    stop_solo_threads()
    localProxy()
    threading.Thread(target = startProxy, daemon=True, name='solo_startProxy').start()
    if init_huggingface():
        start_sync_log_to_huggingface(huggingface_repo)
    load_models(True)
    ticks = time.time()
    print("加载耗时:",(ticks - startTicks),"秒")
    start()


# 执行区域
---

In [ ]:
# 启动
# reLoad = True
# hidden_console_info = False
sys.stdout = sys_sys_stdout
main()

In [ ]:
# 停止一些不必要的后台线程
stop_solo_threads()